In [5]:
import os
import time
import pickle
from collections import deque
from atproto import Client
import keyring
import shutil  # Ensure shutil is imported to avoid NameError

identifier = 'elaval.bsky.social'
password = keyring.get_password('bluesky', identifier)

if not password:
    raise ValueError('No password found in keyring. Please store it first.')

# Initialize the client and log in
client = Client()

try:
    client.login(identifier, password)
    print("Login successful.")
except Exception as e:
    print(f"Login failed: {e}")
    exit(1)  # Exit if login fails

# Parameters
MAX_DEPTH = 3
TOP_N = 5
MIN_FOLLOWERS = 1000
RATE_LIMIT_DELAY = 0.15  # seconds

# File paths
GRAPH_FILE = 'user_graph.pkl'
VISITED_FILE = 'visited_users.pkl'
QUEUE_FILE = 'user_queue.pkl'

# Load or initialize data structures
if os.path.exists(GRAPH_FILE) and os.path.exists(VISITED_FILE) and os.path.exists(QUEUE_FILE):
    with open(GRAPH_FILE, 'rb') as f:
        graph = pickle.load(f)
    with open(VISITED_FILE, 'rb') as f:
        visited = pickle.load(f)
    with open(QUEUE_FILE, 'rb') as f:
        queue = pickle.load(f)
    print("Loaded existing graph, visited set, and queue from files.")
else:
    graph = {}
    visited = set()
    queue = deque()
    print("Starting with a new graph.")

def get_profile(actor):
    """Get the profile information for a given actor (handle or DID)."""
    try:
        print(f"Fetching profile for {actor}...")
        profile = client.get_profile(actor=actor)
        print(f"Fetched profile for {actor}.")
        return profile  # Return the profile object
    except Exception as e:
        print(f"Error fetching profile for {actor}: {e}")
        return None

def get_followers_handles(actor):
    """Get the list of handles that follow the given user."""
    followers_handles = []
    cursor = None
    try:
        print(f"Fetching followers list for {actor}...")
        while True:
            params = {'actor': actor}
            if cursor:
                params['cursor'] = cursor
            # Assuming the client has a method to get followers similar to get_follows
            response = client.get_followers(**params)
            followers = response.followers
            followers_handles.extend([user.handle for user in followers])
            cursor = response.cursor
            if not cursor:
                break
            print(f"Fetched {len(followers)} followers for {actor}, continuing to next page...")
            time.sleep(RATE_LIMIT_DELAY)
        print(f"Fetched total {len(followers_handles)} followers for {actor}.")
        return followers_handles
    except Exception as e:
        print(f"Error fetching followers list for {actor}: {e}")
        return []

def build_graph():
    """Build or update the user graph."""
    total_users_processed = len(visited)
    
    # Step 1: Identify new followers and add them to the front of the queue
    your_handle = 'elaval.bsky.social'
    current_followers = get_followers_handles(your_handle)
    
    # Initialize your own profile in the graph if not present
    if your_handle not in graph:
        your_profile = get_profile(your_handle)
        if your_profile:
            your_followers_count = your_profile.followers_count or 0
            your_avatar_url = your_profile.avatar or ''
            your_description = your_profile.description or ''        # Extract description
            your_display_name = your_profile.display_name or ''      # Extract displayName
        else:
            your_followers_count = 0
            your_avatar_url = ''
            your_description = ''
            your_display_name = ''
        graph[your_handle] = {
            'followers_count': your_followers_count,
            'avatar_url': your_avatar_url,
            'description': your_description,        # Add description to graph
            'displayName': your_display_name,      # Add displayName to graph
            'connections': []
        }
        visited.add(your_handle)  # Mark yourself as visited
        print(f"Added your profile '{your_handle}' to the graph.")
    
    # Identify new followers (not yet visited)
    new_followers = [handle for handle in current_followers if handle not in visited]
    
    if new_followers:
        print(f"Found {len(new_followers)} new follower(s). Adding to the front of the queue.")
        for handle in reversed(new_followers):  # Reverse to maintain order when using appendleft
            queue.appendleft((handle, 1))
    else:
        print("No new followers to add to the queue.")
    
    total_users_in_queue = len(queue)
    print(f"Starting graph build with {total_users_in_queue} users in queue.")
    
    while queue:
        current_handle, depth = queue.popleft()
        total_users_in_queue = len(queue)
    
        if depth > MAX_DEPTH:
            continue
    
        if current_handle in visited:
            continue
    
        visited.add(current_handle)
        total_users_processed += 1
    
        print(f"\nProcessing {current_handle} at depth {depth}...")
        print(f"Total users processed: {total_users_processed}")
        print(f"Users remaining in queue: {total_users_in_queue}")
    
        # Get the profile of the current user
        current_profile = get_profile(current_handle)
        if current_profile:
            current_followers_count = current_profile.followers_count or 0
            current_avatar_url = current_profile.avatar or ''
            current_description = current_profile.description or ''    # Extract description
            current_display_name = current_profile.display_name or ''  # Extract displayName
        else:
            current_followers_count = 0
            current_avatar_url = ''
            current_description = ''
            current_display_name = ''
    
        # Initialize the current user's data in the graph
        graph[current_handle] = {
            'followers_count': current_followers_count,
            'avatar_url': current_avatar_url,
            'description': current_description,        # Add description
            'displayName': current_display_name,      # Add displayName
            'connections': []
        }
    
        # Get the users that the current user is following
        following_handles = get_followers_handles(current_handle)  # Changed to get_followers_handles
    
        # Get follower counts and filter users
        users_data = []
        for index, handle in enumerate(following_handles, start=1):
            if handle not in visited:
                profile = get_profile(handle)
                if profile:
                    followers_count = profile.followers_count or 0
                    avatar_url = profile.avatar or ''
                    description = profile.description or ''        # Extract description
                    display_name = profile.display_name or ''      # Extract displayName
                    if followers_count >= MIN_FOLLOWERS:
                        users_data.append({
                            'handle': handle,
                            'followers_count': followers_count,
                            'avatar_url': avatar_url,
                            'description': description,          # Include description
                            'displayName': display_name         # Include displayName
                        })
                        print(f"User {handle} has {followers_count} followers, added to consideration.")
                    else:
                        print(f"User {handle} has {followers_count} followers, below threshold.")
                    time.sleep(RATE_LIMIT_DELAY)
                else:
                    print(f"Profile not found for {handle}.")
            else:
                print(f"User {handle} already visited.")
            if index % 10 == 0:
                print(f"Processed {index} out of {len(following_handles)} follows for {current_handle}.")
    
        # Sort and select top N users
        top_users = sorted(users_data, key=lambda x: x['followers_count'], reverse=True)[:TOP_N]
    
        # Add edges to the graph
        for user in top_users:
            handle = user['handle']
            avatar_url = user['avatar_url']
            followers_count = user['followers_count']
            description = user['description']      # Get description
            display_name = user['displayName']     # Get displayName
    
            graph[current_handle]['connections'].append(handle)
    
            if handle not in graph:
                graph[handle] = {
                    'followers_count': followers_count,
                    'avatar_url': avatar_url,
                    'description': description,        # Add description
                    'displayName': display_name,      # Add displayName
                    'connections': []
                }
    
            queue.append((handle, depth + 1))
            print(f"Added {handle} to queue with {followers_count} followers.")
    
        print(f"Completed processing of {current_handle}.")
    
        # Save the state after processing each user
        with open(GRAPH_FILE, 'wb') as f:
            pickle.dump(graph, f)
        with open(VISITED_FILE, 'wb') as f:
            pickle.dump(visited, f)
        with open(QUEUE_FILE, 'wb') as f:
            pickle.dump(queue, f)
    
    print("Graph building complete.")

build_graph()


Login successful.
Loaded existing graph, visited set, and queue from files.
Fetching followers list for elaval.bsky.social...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50 followers for elaval.bsky.social, continuing to next page...
Fetched 50

Fetching profile for giovannaofficial.bsky.social...
Fetched profile for giovannaofficial.bsky.social.
User giovannaofficial.bsky.social has 40 followers, below threshold.
Fetching profile for shahidazmi9924.bsky.social...
Fetched profile for shahidazmi9924.bsky.social.
User shahidazmi9924.bsky.social has 8315 followers, added to consideration.
Fetching profile for snslyla.bsky.social...
Fetched profile for snslyla.bsky.social.
User snslyla.bsky.social has 151 followers, below threshold.
Fetching profile for syedshahidikram.bsky.social...
Fetched profile for syedshahidikram.bsky.social.
User syedshahidikram.bsky.social has 1424 followers, added to consideration.
Fetching profile for mehedyhasanromjan.bsky.social...
Fetched profile for mehedyhasanromjan.bsky.social.
User mehedyhasanromjan.bsky.social has 1050 followers, added to consideration.
Fetching profile for khalil0mer.bsky.social...
Fetched profile for khalil0mer.bsky.social.
User khalil0mer.bsky.social has 1970 followers, added 

Fetching profile for out-of-context-wrd.bsky.social...
Fetched profile for out-of-context-wrd.bsky.social.
User out-of-context-wrd.bsky.social has 2601 followers, added to consideration.
Fetching profile for arshadsalim78.bsky.social...
Fetched profile for arshadsalim78.bsky.social.
User arshadsalim78.bsky.social has 1157 followers, added to consideration.
Fetching profile for sk8rrbaee.bsky.social...
Fetched profile for sk8rrbaee.bsky.social.
User sk8rrbaee.bsky.social has 217 followers, below threshold.
Fetching profile for chrisdeloge.bsky.social...
Fetched profile for chrisdeloge.bsky.social.
User chrisdeloge.bsky.social has 511 followers, below threshold.
Fetching profile for mrswest.bsky.social...
Fetched profile for mrswest.bsky.social.
User mrswest.bsky.social has 1687 followers, added to consideration.
Fetching profile for gooodkarma.bsky.social...
Fetched profile for gooodkarma.bsky.social.
User gooodkarma.bsky.social has 820 followers, below threshold.
Fetching profile for p

Fetched profile for freddierose.bsky.social.
User freddierose.bsky.social has 10709 followers, added to consideration.
Fetching profile for lebergerdavid.bsky.social...
Fetched profile for lebergerdavid.bsky.social.
User lebergerdavid.bsky.social has 1953 followers, added to consideration.
Fetching profile for scottasantee.bsky.social...
Fetched profile for scottasantee.bsky.social.
User scottasantee.bsky.social has 1646 followers, added to consideration.
Fetching profile for gmckeon.bsky.social...
Fetched profile for gmckeon.bsky.social.
User gmckeon.bsky.social has 477 followers, below threshold.
Fetching profile for catmumof2.bsky.social...
Fetched profile for catmumof2.bsky.social.
User catmumof2.bsky.social has 2665 followers, added to consideration.
Fetching profile for ahmadkhanlive.bsky.social...
Fetched profile for ahmadkhanlive.bsky.social.
User ahmadkhanlive.bsky.social has 19167 followers, added to consideration.
Fetching profile for inkfreq.com...
Fetched profile for inkfr

Processed 180 out of 297 follows for aliuejatta.bsky.social.
Fetching profile for hussam94.bsky.social...
Fetched profile for hussam94.bsky.social.
User hussam94.bsky.social has 3739 followers, added to consideration.
Fetching profile for miamalkova01.bsky.social...
Fetched profile for miamalkova01.bsky.social.
User miamalkova01.bsky.social has 516 followers, below threshold.
Fetching profile for sofialipti.bsky.social...
Fetched profile for sofialipti.bsky.social.
User sofialipti.bsky.social has 20820 followers, added to consideration.
Fetching profile for bit.bsky.social...
Fetched profile for bit.bsky.social.
User bit.bsky.social has 1339 followers, added to consideration.
Fetching profile for liberallylv.bsky.social...
Fetched profile for liberallylv.bsky.social.
User liberallylv.bsky.social has 1658 followers, added to consideration.
Fetching profile for moh36ps.bsky.social...
Fetched profile for moh36ps.bsky.social.
User moh36ps.bsky.social has 1103 followers, added to considerat

...

Fetching profile for 71saj.bsky.social...
Fetched profile for 71saj.bsky.social.
User 71saj.bsky.social has 826 followers, below threshold.
Processed 3710 out of 8094 follows for khan-official.bsky.social.
Fetching profile for diana-adnan.bsky.social...
Fetched profile for diana-adnan.bsky.social.
User diana-adnan.bsky.social has 3043 followers, added to consideration.
Fetching profile for geneleis.bsky.social...
Fetched profile for geneleis.bsky.social.
User geneleis.bsky.social has 585 followers, below threshold.
Fetching profile for saetediattara.bsky.social...
Fetched profile for saetediattara.bsky.social.
User saetediattara.bsky.social has 291 followers, below threshold.
Fetching profile for jeannotusa.bsky.social...
Fetched profile for jeannotusa.bsky.social.
User jeannotusa.bsky.social has 72 followers, below threshold.
Fetching profile for jedirepublicano.bsky.social...
Fetched profile for jedirepublicano.bsky.social.
User jedirepublicano.bsky.social has 629 followers, below th

Fetched profile for missnafessaah.bsky.social.
User missnafessaah.bsky.social has 416 followers, below threshold.
Processed 3760 out of 8094 follows for khan-official.bsky.social.
Fetching profile for basrabhai.bsky.social...
Fetched profile for basrabhai.bsky.social.
User basrabhai.bsky.social has 2296 followers, added to consideration.
Fetching profile for csapmi.bsky.social...
Fetched profile for csapmi.bsky.social.
User csapmi.bsky.social has 10897 followers, added to consideration.
Fetching profile for shafiq78.bsky.social...
Fetched profile for shafiq78.bsky.social.
User shafiq78.bsky.social has 193 followers, below threshold.
Fetching profile for issa-ndi.bsky.social...
Fetched profile for issa-ndi.bsky.social.
User issa-ndi.bsky.social has 1155 followers, added to consideration.
Fetching profile for raine69.bsky.social...
Fetched profile for raine69.bsky.social.
User raine69.bsky.social has 1982 followers, added to consideration.
Fetching profile for spidergoat0.bsky.social...


Fetching profile for pjoy26.bsky.social...
Fetched profile for pjoy26.bsky.social.
User pjoy26.bsky.social has 1915 followers, added to consideration.
Processed 3810 out of 8094 follows for khan-official.bsky.social.
Fetching profile for lisadiffenbaugh.bsky.social...
Fetched profile for lisadiffenbaugh.bsky.social.
User lisadiffenbaugh.bsky.social has 459 followers, below threshold.
Fetching profile for omahamaverick.bsky.social...
Fetched profile for omahamaverick.bsky.social.
User omahamaverick.bsky.social has 363 followers, below threshold.
Fetching profile for ndiouga4.bsky.social...
Fetched profile for ndiouga4.bsky.social.
User ndiouga4.bsky.social has 1143 followers, added to consideration.
Fetching profile for jdtahirppp.bsky.social...
Fetched profile for jdtahirppp.bsky.social.
User jdtahirppp.bsky.social has 232 followers, below threshold.
Fetching profile for youryka.bsky.social...
Fetched profile for youryka.bsky.social.
User youryka.bsky.social has 992 followers, below th

Fetching profile for gulzadakhan.bsky.social...
Fetched profile for gulzadakhan.bsky.social.
User gulzadakhan.bsky.social has 134 followers, below threshold.
Processed 3860 out of 8094 follows for khan-official.bsky.social.
Fetching profile for jaarah.bsky.social...
Fetched profile for jaarah.bsky.social.
User jaarah.bsky.social has 1009 followers, added to consideration.
Fetching profile for rustam12.bsky.social...
Fetched profile for rustam12.bsky.social.
User rustam12.bsky.social has 329 followers, below threshold.
Fetching profile for theegaleofiqbal.bsky.social...
Fetched profile for theegaleofiqbal.bsky.social.
User theegaleofiqbal.bsky.social has 672 followers, below threshold.
Fetching profile for passanejr.bsky.social...
Fetched profile for passanejr.bsky.social.
User passanejr.bsky.social has 245 followers, below threshold.
Fetching profile for ishtiaqbaryar.bsky.social...
Fetched profile for ishtiaqbaryar.bsky.social.
User ishtiaqbaryar.bsky.social has 331 followers, below t

KeyboardInterrupt: 

In [ ]:
# Install required packages if not already installed
!pip install atproto keyring tqdm

# Import necessary libraries
import os
import time
import pickle
from collections import deque
from atproto import Client
import keyring
import shutil
import logging
from tqdm import tqdm  # Import tqdm for the progress bar
import signal
import sys
import datetime

# Configuration
IDENTIFIER = 'elaval.bsky.social'
RATE_LIMIT_DELAY = 0.15  # seconds between API calls to respect rate limits

# File paths
GRAPH_FILE = 'user_graph.pkl'
BACKUP_FILE = 'user_graph_backup.pkl'
VISITED_FILE = 'visited.pkl'
QUEUE_FILE = 'queue.pkl'
LOG_FILE = 'update_followers.log'  # Log file for tracking updates

# Default avatar URL (optional, in case you want to handle missing avatars)
DEFAULT_AVATAR = 'https://example.com/default_avatar.png'  # Replace with your default avatar URL

# Constants for graph building
MAX_DEPTH = 3         # Define how deep the traversal should go
TOP_N = 10            # Number of top followers to consider at each level
MIN_FOLLOWERS = 1000  # Minimum number of followers a user must have to be considered

# Configure logging
logging.basicConfig(
    filename=LOG_FILE,  # Log output to a file
    level=logging.INFO,  # Logging level
    format='%(asctime)s - %(levelname)s - %(message)s'  # Log format
)

# Global variables to hold the graph, visited set, and queue for signal handling
graph = {}
visited = set()
queue = deque()

def save_state(graph, visited, queue):
    """Save the current state of the graph, visited set, and queue."""
    try:
        with open(GRAPH_FILE, 'wb') as f:
            pickle.dump(graph, f)
        with open(VISITED_FILE, 'wb') as f:
            pickle.dump(visited, f)
        with open(QUEUE_FILE, 'wb') as f:
            pickle.dump(queue, f)
        logging.info("Saved graph, visited set, and queue state.")
    except Exception as e:
        logging.error(f"Error saving state: {e}")
        print(f"Error saving state: {e}")

def signal_handler(sig, frame):
    print('\nUpdate interrupted. Saving progress...')
    logging.info('Update interrupted by user.')
    save_state(graph, visited, queue)  # Save all states
    sys.exit(0)

# Register the signal handler for graceful interruption
signal.signal(signal.SIGINT, signal_handler)

def get_profile(client, actor):
    """Fetch the profile information for a given actor (handle or DID)."""
    try:
        logging.info(f"Fetching profile for {actor}...")
        profile = client.get_profile(actor=actor)
        logging.info(f"Fetched profile for {actor}.")
        return profile  # Return the profile object
    except Exception as e:
        logging.error(f"Error fetching profile for {actor}: {e}")
        return None

def get_followers_handles(client, actor):
    """Get the list of handles that follow the given user."""
    followers_handles = []
    cursor = None
    try:
        logging.info(f"Fetching followers list for {actor}...")
        while True:
            params = {'actor': actor, 'limit': 50}
            if cursor:
                params['cursor'] = cursor
            response = client.get_followers(**params)
            followers = response.followers
            followers_handles.extend([user.handle for user in followers])
            cursor = response.cursor
            if not cursor:
                break
            logging.info(f"Fetched {len(followers)} followers for {actor}, continuing to next page...")
            time.sleep(RATE_LIMIT_DELAY)
        logging.info(f"Fetched total {len(followers_handles)} followers for {actor}.")
        return followers_handles
    except Exception as e:
        logging.error(f"Error fetching followers list for {actor}: {e}")
        return []

def build_graph(client, graph, visited, queue):
    """Build or update the user graph."""
    total_users_processed = len(visited)
    
    # Step 1: Identify new followers and add them to the front of the queue
    your_handle = IDENTIFIER
    current_followers = get_followers_handles(client, your_handle)
    
    # Initialize your own profile in the graph if not present
    if your_handle not in graph:
        your_profile = get_profile(client, your_handle)
        if your_profile:
            your_followers_count = your_profile.followers_count or 0
            your_avatar_url = your_profile.avatar or DEFAULT_AVATAR
            your_description = your_profile.description or ''        # Extract description
            your_display_name = your_profile.display_name or ''      # Extract displayName
        else:
            your_followers_count = 0
            your_avatar_url = DEFAULT_AVATAR
            your_description = ''
            your_display_name = ''
        graph[your_handle] = {
            'followers_count': your_followers_count,
            'avatar_url': your_avatar_url,
            'description': your_description,        # Add description to graph
            'displayName': your_display_name,      # Add displayName to graph
            'connections': []
        }
        visited.add(your_handle)  # Mark yourself as visited
        logging.info(f"Added your profile '{your_handle}' to the graph.")
        print(f"Added your profile '{your_handle}' to the graph.")
    
    # Identify new followers (not yet visited)
    new_followers = [handle for handle in current_followers if handle not in visited]
    
    if new_followers:
        logging.info(f"Found {len(new_followers)} new follower(s). Adding to the front of the queue.")
        print(f"Found {len(new_followers)} new follower(s). Adding to the front of the queue.")
        for handle in reversed(new_followers):  # Reverse to maintain order when using appendleft
            queue.appendleft((handle, 1))
    else:
        logging.info("No new followers to add to the queue.")
        print("No new followers to add to the queue.")
    
    total_users_in_queue = len(queue)
    logging.info(f"Starting graph build with {total_users_in_queue} users in queue.")
    print(f"Starting graph build with {total_users_in_queue} users in queue.")
    
    # Initialize tqdm progress bar
    with tqdm(total=total_users_in_queue, desc="Processing Users", unit="user") as pbar:
        while queue:
            current_handle, depth = queue.popleft()
            total_users_in_queue = len(queue)

            if depth > MAX_DEPTH:
                pbar.update(1)
                continue

            if current_handle in visited:
                pbar.update(1)
                continue

            visited.add(current_handle)
            total_users_processed += 1

            logging.info(f"\nProcessing {current_handle} at depth {depth}...")
            print(f"\nProcessing {current_handle} at depth {depth}...")
            print(f"Total users processed: {total_users_processed}")
            print(f"Users remaining in queue: {total_users_in_queue}")

            # Get the profile of the current user
            current_profile = get_profile(client, current_handle)
            if current_profile:
                current_followers_count = current_profile.followers_count or 0
                current_avatar_url = current_profile.avatar or DEFAULT_AVATAR
                current_description = current_profile.description or ''    # Extract description
                current_display_name = current_profile.display_name or ''  # Extract displayName
            else:
                current_followers_count = 0
                current_avatar_url = DEFAULT_AVATAR
                current_description = ''
                current_display_name = ''

            # Initialize the current user's data in the graph
            graph[current_handle] = {
                'followers_count': current_followers_count,
                'avatar_url': current_avatar_url,
                'description': current_description,        # Add description
                'displayName': current_display_name,      # Add displayName
                'connections': []
            }

            # Get the followers of the current user
            following_handles = get_followers_handles(client, current_handle)

            # Get follower counts and filter users
            users_data = []
            for index, handle in enumerate(following_handles, start=1):
                if handle not in visited:
                    profile = get_profile(client, handle)
                    if profile:
                        followers_count = profile.followers_count or 0
                        avatar_url = profile.avatar or DEFAULT_AVATAR
                        description = profile.description or ''        # Extract description
                        display_name = profile.display_name or ''      # Extract displayName
                        if followers_count >= MIN_FOLLOWERS:
                            users_data.append({
                                'handle': handle,
                                'followers_count': followers_count,
                                'avatar_url': avatar_url,
                                'description': description,          # Include description
                                'displayName': display_name         # Include displayName
                            })
                            logging.info(f"User {handle} has {followers_count} followers, added to consideration.")
                            print(f"User {handle} has {followers_count} followers, added to consideration.")
                        else:
                            logging.info(f"User {handle} has {followers_count} followers, below threshold.")
                            print(f"User {handle} has {followers_count} followers, below threshold.")
                        time.sleep(RATE_LIMIT_DELAY)
                    else:
                        logging.info(f"Profile not found for {handle}.")
                        print(f"Profile not found for {handle}.")
                else:
                    logging.info(f"User {handle} already visited.")
                    print(f"User {handle} already visited.")
                if index % 10 == 0:
                    logging.info(f"Processed {index} out of {len(following_handles)} follows for {current_handle}.")
                    print(f"Processed {index} out of {len(following_handles)} follows for {current_handle}.")

            # Sort and select top N users
            top_users = sorted(users_data, key=lambda x: x['followers_count'], reverse=True)[:TOP_N]

            # Add edges to the graph
            for user in top_users:
                handle = user['handle']
                avatar_url = user['avatar_url']
                followers_count = user['followers_count']
                description = user['description']      # Get description
                display_name = user['displayName']     # Get displayName

                graph[current_handle]['connections'].append(handle)

                if handle not in graph:
                    graph[handle] = {
                        'followers_count': followers_count,
                        'avatar_url': avatar_url,
                        'description': description,        # Add description
                        'displayName': display_name,      # Add displayName
                        'connections': []
                    }

                queue.append((handle, depth + 1))
                logging.info(f"Added {handle} to queue with {followers_count} followers.")
                print(f"Added {handle} to queue with {followers_count} followers.")

            logging.info(f"Completed processing of {current_handle}.")
            print(f"Completed processing of {current_handle}.")

            # Update the progress bar
            pbar.update(1)

            # Save the state after processing each user
            save_state(graph, visited, queue)

def main():
    global graph, visited, queue

    # Retrieve password from keyring
    password = keyring.get_password('bluesky', IDENTIFIER)

    if not password:
        logging.error('No password found in keyring. Please store it first.')
        print('No password found in keyring. Please store it first.')
        raise ValueError('No password found in keyring. Please store it first.')

    # Initialize the client and log in
    client = Client()

    try:
        client.login(IDENTIFIER, password)
        logging.info("Login successful.")
        print("Login successful.")
    except Exception as e:
        logging.error(f"Login failed: {e}")
        print(f"Login failed: {e}")
        raise e  # Exit the script if login fails

    # Backup the original pickle file
    try:
        if os.path.exists(GRAPH_FILE):
            shutil.copyfile(GRAPH_FILE, BACKUP_FILE)
            logging.info(f"Backup created at '{BACKUP_FILE}'.")
            print(f"Backup created at '{BACKUP_FILE}'.")
    except Exception as e:
        logging.error(f"Error creating backup: {e}")
        print(f"Error creating backup: {e}")
        raise e

    # Load the graph data
    if os.path.exists(GRAPH_FILE):
        with open(GRAPH_FILE, 'rb') as f:
            try:
                graph = pickle.load(f)
                logging.info(f"Successfully loaded '{GRAPH_FILE}'.")
                print(f"Successfully loaded '{GRAPH_FILE}'.")
            except Exception as e:
                logging.error(f"Error loading pickle file: {e}")
                print(f"Error loading pickle file: {e}")
                raise e
    else:
        graph = {}
        logging.info(f"No existing graph file found. Starting fresh.")
        print(f"No existing graph file found. Starting fresh.")

    # Load or initialize visited and queue
    if os.path.exists(VISITED_FILE) and os.path.exists(QUEUE_FILE):
        with open(VISITED_FILE, 'rb') as f:
            visited = pickle.load(f)
        with open(QUEUE_FILE, 'rb') as f:
            queue = pickle.load(f)
        logging.info("Loaded existing visited set and queue from files.")
        print("Loaded existing visited set and queue from files.")
    else:
        visited = set()
        queue = deque()
        logging.info("Starting with an empty visited set and queue.")
        print("Starting with an empty visited set and queue.")

    # **Call the build_graph function with the right parameters**
    build_graph(client, graph, visited, queue)

    # Save the updated graph
    try:
        save_state(graph, visited, queue)
        logging.info(f"Graph updated successfully. Check '{GRAPH_FILE}' and '{LOG_FILE}' for details.")
        print(f"Graph updated successfully. Check '{GRAPH_FILE}' and '{LOG_FILE}' for details.")
    except Exception as e:
        logging.error(f"Failed to save updated graph: {e}")
        print(f"Failed to save updated graph: {e}")
        raise e

# Execute the main function
main()


Defaulting to user installation because normal site-packages is not writeable
  Using cached atproto-0.0.55-py3-none-any.whl.metadata (14 kB)
  Using cached dnspython-2.7.0-py3-none-any.whl.metadata (5.8 kB)
Using cached atproto-0.0.55-py3-none-any.whl (327 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.2/6.2 MB 6.2 MB/s eta 0:00:00a 0:00:01
Using cached dnspython-2.7.0-py3-none-any.whl (313 kB)
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.

[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: /Applications/Xcode.app/Contents/Developer/usr/bin/python3 -m pip install --upgrade pip
Login successful.
Backup created at 'user_graph_backup.pkl'.
Successfully loaded 'user_graph.pkl'.
Starting with an empty visited set and queue.
Found 814 new follower(s). Adding to the front o

Processing Users:   0%|                               | 0/814 [00:00<?, ?user/s]


Processing joromero.bsky.social at depth 1...
Total users processed: 1
Users remaining in queue: 813


Processing Users:   0%|                       | 1/814 [00:00<09:29,  1.43user/s]

Completed processing of joromero.bsky.social.

Processing pamerp.bsky.social at depth 1...
Total users processed: 2
Users remaining in queue: 812
User danih1982.bsky.social has 96 followers, below threshold.
User andykingsx.bsky.social has 1269 followers, added to consideration.
User hablamosdetodo.bsky.social has 2294 followers, added to consideration.
User laibayt668.bsky.social has 6703 followers, added to consideration.
User mazaciclismo.bsky.social has 1240 followers, added to consideration.
User h0ttieebaee.bsky.social has 203 followers, below threshold.
User lovirae.bsky.social has 9474 followers, added to consideration.
User alegriagonzaa.bsky.social has 1293 followers, added to consideration.
User crimeajewel.bsky.social has 23769 followers, added to consideration.
User katalinaparis.bsky.social has 335 followers, below threshold.
Processed 10 out of 11 follows for pamerp.bsky.social.


...

User jonnyporras.bsky.social has 41 followers, below threshold.
User alv4.bsky.social has 414 followers, below threshold.
User odisseo.bsky.social has 482 followers, below threshold.
User manumontv.bsky.social has 880 followers, below threshold.
User mikeeldemonio.bsky.social has 1631 followers, added to consideration.
User siskofernandez.bsky.social has 591 followers, below threshold.
User erikalopezsoto.bsky.social has 35 followers, below threshold.
User gabrielsan34.bsky.social has 1050 followers, added to consideration.
User kye1925.bsky.social has 6411 followers, added to consideration.
User ardeban.and.lgbt has 605 followers, below threshold.
Processed 230 out of 799 follows for infozeus.bsky.social.
User tochernan.bsky.social has 781 followers, below threshold.
User ddarko1980.bsky.social has 381 followers, below threshold.
User mahogay88.bsky.social has 337 followers, below threshold.
User crj17.bsky.social has 139 followers, below threshold.
User pablo5700.bsky.social has 204 

User had3091.bsky.social has 318 followers, below threshold.
User jorgespadas.bsky.social has 2195 followers, added to consideration.
Processed 340 out of 799 follows for infozeus.bsky.social.
User johnpito.bsky.social has 525 followers, below threshold.
User nachoamaya.bsky.social has 487 followers, below threshold.
User beardedenough.bsky.social has 38 followers, below threshold.
User crimeajewel.bsky.social has 23771 followers, added to consideration.
User ignace.bsky.social has 257 followers, below threshold.
User carogl.bsky.social has 193 followers, below threshold.
User jjpato1919.bsky.social has 4 followers, below threshold.
User sirtan.bsky.social has 10636 followers, added to consideration.
User fitfirst.bsky.social has 8821 followers, added to consideration.
User marielepichon.bsky.social has 17 followers, below threshold.
Processed 350 out of 799 follows for infozeus.bsky.social.
User negritamarcela.bsky.social has 872 followers, below threshold.
User krpofficial.bsky.socia

User anyanez91.bsky.social has 449 followers, below threshold.
User kevinet.bsky.social has 500 followers, below threshold.
User aldeanopromedio.bsky.social has 402 followers, below threshold.
User sameerrraed.bsky.social has 3827 followers, added to consideration.
User rataiz.bsky.social has 170 followers, below threshold.
User lapaulanomas.bsky.social has 43 followers, below threshold.
Processed 460 out of 799 follows for infozeus.bsky.social.
User peropedro.bsky.social has 552 followers, below threshold.
User lacalamitosa.bsky.social has 128 followers, below threshold.
User semiarido.bsky.social has 135 followers, below threshold.
User brunoivanmore.bsky.social has 39 followers, below threshold.
User jose4545.bsky.social has 341 followers, below threshold.
User drcaribu.bsky.social has 81 followers, below threshold.
User sebavalat.bsky.social has 762 followers, below threshold.
User marioisalinas.bsky.social has 111 followers, below threshold.
User alekojpg.bsky.social has 2657 foll

User nwbwr.bsky.social has 282 followers, below threshold.
User abandior.bsky.social has 75 followers, below threshold.
User animaritos.bsky.social has 632 followers, below threshold.
User alainmlg97.bsky.social has 295 followers, below threshold.
User danicarpio.bsky.social has 1423 followers, added to consideration.
User drsylvain.bsky.social has 1219 followers, added to consideration.
User lenoxalmonacid.bsky.social has 520 followers, below threshold.
User lapaula.bsky.social has 555 followers, below threshold.
User carlosdeeguiluz.bsky.social has 2455 followers, added to consideration.
Processed 580 out of 799 follows for infozeus.bsky.social.
User eddsos.bsky.social has 873 followers, below threshold.
User donimcleod.bsky.social has 112 followers, below threshold.
User vicsversion.bsky.social has 871 followers, below threshold.
User josev11.bsky.social has 535 followers, below threshold.
User soundoodles.bsky.social has 4498 followers, added to consideration.
User dulcepkadora.bsk

User chrstnf.bsky.social has 53 followers, below threshold.
User blasstter.bsky.social has 486 followers, below threshold.
Processed 690 out of 799 follows for infozeus.bsky.social.
User phagop.bsky.social has 8956 followers, added to consideration.
User villalobosjara.bsky.social has 714 followers, below threshold.
User im2fat4you.bsky.social has 210 followers, below threshold.
User mprojo.bsky.social has 574 followers, below threshold.
User nnefelibato.bsky.social has 1142 followers, added to consideration.
User caminarto.bsky.social has 94 followers, below threshold.
User fichi.bsky.social has 589 followers, below threshold.
User ankorinclan.es has 2637 followers, added to consideration.
User suponjisan.bsky.social has 268 followers, below threshold.
User vicgramar89.bsky.social has 459 followers, below threshold.
Processed 700 out of 799 follows for infozeus.bsky.social.
User eric-zolanski.bsky.social has 397 followers, below threshold.
User mattyll.bsky.social has 3730 followers, 